In [2]:
%pip install --upgrade --quiet  langchain langchain-community langchain-openai langchain-experimental neo4j tiktoken yfiles_jupyter_graphs
!pip install langchain_groq
!pip install python-dotenv



Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
from langchain_community.vectorstores import Neo4jVector
# from yfiles_jupyter_graphs import GraphWidget
from neo4j import GraphDatabase
from typing import Tuple, List, Optional
import os
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import DirectoryLoader , CSVLoader
from langchain_community.graphs import Neo4jGraph


In [ ]:
NEO4J_URI=
NEO4J_USERNAME="neo4j"
NEO4J_PASSWORD=
GROQ_API_KEY = 


In [4]:
os.environ["NEO4J_URI"] = NEO4J_URI
os.environ["NEO4J_USERNAME"] = NEO4J_USERNAME
os.environ["NEO4J_PASSWORD"] = NEO4J_PASSWORD

In [7]:
graph = Neo4jGraph()

In [5]:
import pandas as pd

# Load the data into a pandas DataFrame
df = pd.read_csv("data/nhs_disease_components.csv")

# Remove empty or blank values
df = df[~df["name"].isin(['', "nan"]) & ~df["link"].isin(['', "nan"]) & ~df["About"].isin(['', "nan"])]

# Normalize the data
df["name"] = df["name"].str.strip().str.lower()
df["About"] = df["About"].str.strip().str.lower()

# Write the cleaned data back to a file
df.to_csv("data/nhs_disease_components.csv", index=False)


FileNotFoundError: [Errno 2] No such file or directory: 'data/nhs_disease_components.csv'

In [19]:
# Extract data from the docs

def load_data(file_path):
  loader = DirectoryLoader(
      file_path,
      glob="**/*.csv",
      loader_cls=CSVLoader,
      loader_kwargs={"encoding": "utf-8"} 
  )
  documents = loader.load()
  return documents

In [20]:

documents = load_data("demo_data")


In [21]:
documents

[Document(metadata={'source': 'demo_data\\nhs_disease_components.csv', 'row': 0}, page_content="name: abdominal aortic aneurysm\nlink: https://www.nhsinform.scot/illnesses-and-conditions/cardiovascular-disease/heart-disease/abdominal-aortic-aneurysm/\nAbout: [{'about abdominal aortic aneurysms': ' an abdominal aortic aneurysm (aaa) is a swelling (aneurysm) of the aorta – the main blood vessel that leads away from the heart, down through the abdomen to the rest of the body. the abdominal aorta is the largest blood vessel in the body and is usually around 2cm wide – roughly the width of a garden hose. however, it can swell to over 5.5cm – what doctors class as a large aaa. large aneurysms are rare, but can be very serious. if a large aneurysm bursts, it causes huge internal bleeding and is usually fatal. the bulging occurs when the wall of the aorta weakens. although what causes this weakness is unclear, smoking and high blood pressure are thought to increase the risk of an aneurysm. aaa

In [24]:
#  create text chunks

def create_text_chunks(documents):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size = 4000,
        chunk_overlap = 0,
        length_function = len,
        keep_separator=True,
        add_start_index=True,
        strip_whitespace=True,
    )
    chunks = text_splitter.split_documents(documents)
    return chunks


In [25]:
text_chunks = create_text_chunks(documents)
print(len(text_chunks))

1052


In [30]:
from langchain_groq import ChatGroq
from dotenv import load_dotenv
load_dotenv()

os.environ["GROQ_API_KEY"] = GROQ_API_KEY
def load_model():
    llm = ChatGroq(
        model="gemma2-9b-it",
        temperature=0
    )
    return llm

In [31]:
llm = load_model()

In [32]:
from langchain_experimental.graph_transformers import LLMGraphTransformer
llm_transformer = LLMGraphTransformer(
    llm=llm,
    allowed_nodes=[
        "Disease",
        "Symptom",
        "Cause",
        "RiskFactor",
        "Diagnosis",
        "Doctor",
        "Treatment",
        "Medication",
        "MedicalTest"
    ],
    allowed_relationships=[
        "HAS_SYMPTOM",
        "HAS_CAUSE",
        "HAS_RISK_FACTOR",
        "HAS_DIAGNOSIS",
        "CONSULT_WITH",
        "TREATED_BY",
        "PRESCRIBED",
        "DIAGNOSED_BY"
    ]
)


In [33]:

graph_documents = llm_transformer.convert_to_graph_documents(text_chunks)

BadRequestError: Error code: 400 - {'error': {'message': "Failed to call a function. Please adjust your prompt. See 'failed_generation' for more details.", 'type': 'invalid_request_error', 'code': 'tool_use_failed', 'failed_generation': '<tool-use>\n{\n\t"tool_call": {\n\t\t"id": "pending",\n\t\t"type": "function",\n\t\t"function": {\n\t\t\t"name": "DynamicGraph"\n\t\t},\n\t\t"parameters": {\n\t\t\t"nodes": [\n\t\t\t\t{\n\t\t\t\t\t"id": "grade 1",\n\t\t\t\t\t"type": "Symptom"\n\t\t\t\t},\n\t\t\t\t{\n\t\t\t\t\t"id": "grade 2",\n\t\t\t\t\t"type": "Symptom"\n\t\t\t\t},\n\t\t\t\t{\n\t\t\t\t\t"id": "grade 3",\n\t\t\t\t\t"type": "Symptom"\n\t\t\t\t},\n\t\t\t\t{\n\t\t\t\t\t"id": "grade 4",\n\t\t\t\t\t"type": "Symptom"\n\t\t\t\t},\n\t\t\t\t{\n\t\t\t\t\t"id": "whiteheads",\n\t\t\t\t\t"type": "Disease"\n\t\t\t\t},\n\t\t\t\t{\n\t\t\t\t\t"id": "blackheads",\n\t\t\t\t\t"type": "Disease"\n\t\t\t\t},\n\t\t\t\t{\n\t\t\t\t\t"id": "papules",\n\t\t\t\t\t"type": "Disease"\n\t\t\t\t},\n\t\t\t\t{\n\t\t\t\t\

In [20]:
graph_documents

[GraphDocument(nodes=[Node(id='Acanthosis Nigricans', type='Disease')], relationships=[], source=Document(metadata={'source': 'data\\cleaned_disease_components.csv', 'row': 0, 'start_index': 0}, page_content='name: acanthosis nigricans\nlink: https://www.mayoclinic.org/diseases-conditions/acanthosis-nigricans/symptoms-causes/syc-20368983\nsymptoms: ["skin changes are the only signs of acanthosis nigricans. you\'ll notice dark, thickened, velvety skin in body folds and creases — typically in your armpits, groin and back of the neck. the skin changes usually appear slowly. the affected skin may also have an odor or itch.", \'consult your doctor if you notice changes in your skin — especially if the changes appear suddenly. you may have an underlying condition that needs treatment.\', \'\', \'\', \'\']\noverview: [\'\', \'acanthosis nigricans is a skin condition that causes a dark discoloration in body folds and creases. it typically affects the armpits, groin and neck.\', \'\', \'acantho

In [23]:
graph.add_graph_documents(
    graph_documents,
    baseEntityLabel=True,
    include_source=True
)

In [45]:
def create_disease_graph(tx, disease_name, symptoms, overview, causes, risk_factors, diagnosis):
    # Create Disease Node
    tx.run("MERGE (d:Disease {name: $disease_name})", disease_name=disease_name)
    
    # Create Overview Node
    if overview:
        tx.run("MERGE (o:overview {description: $overview}) "
               "MERGE (d:disease {name: $disease_name})-[:HAS_OVERVIEW]->(o)",
               overview=overview, disease_name=disease_name)
    
    # Create Symptom Nodes and Relationships
    for symptom in symptoms:
        tx.run("MERGE (s:Symptom {name: $symptom}) "
               "MERGE (d:Disease {name: $disease_name})-[:HAS_SYMPTOM]->(s)",
               symptom=symptom, disease_name=disease_name)
    
    # Create Cause Nodes and Relationships
    for cause in causes:
        tx.run("MERGE (c:Cause {description: $cause}) "
               "MERGE (d:Disease {name: $disease_name})-[:HAS_CAUSE]->(c)",
               cause=cause, disease_name=disease_name)
    
    # Create Risk Factor Nodes and Relationships
    for risk_factor in risk_factors:
        tx.run("MERGE (r:RiskFactor {description: $risk_factor}) "
               "MERGE (d:Disease {name: $disease_name})-[:HAS_RISK_FACTOR]->(r)",
               risk_factor=risk_factor, disease_name=disease_name)
    
    # Create Diagnosis Nodes and Relationships
    for diag in diagnosis:
        tx.run("MERGE (diag:Diagnosis {description: $diagnosis}) "
               "MERGE (d:Disease {name: $disease_name})-[:HAS_DIAGNOSIS]->(diag)",
               diagnosis=diag, disease_name=disease_name)

In [66]:
import pandas as pd
import ast
from io import StringIO


In [75]:

# Load the CSV file into a DataFrame
df = pd.read_csv('data/disease_components.csv',  on_bad_lines='skip')

# Display the first few rows of the DataFrame
print(df.head())


                      name                                               link  \
0     Acanthosis nigricans  https://www.mayoclinic.org/diseases-conditions...   
1                Achalasia  https://www.mayoclinic.org/diseases-conditions...   
2  Achilles tendon rupture  https://www.mayoclinic.org/diseases-conditions...   
3  Acute coronary syndrome  https://www.mayoclinic.org/diseases-conditions...   
4              Adenomyosis  https://www.mayoclinic.org/diseases-conditions...   

                                            Symptoms  \
0  ["Skin changes are the only signs of acanthosi...   
1  ['Achalasia symptoms generally appear graduall...   
2  ["Although it's possible to have no signs or s...   
3  ['The signs and symptoms of acute coronary syn...   
4  ['Sometimes, adenomyosis causes no signs or sy...   

                                            Overview  \
0  ['', 'Acanthosis nigricans is a skin condition...   
1  ['Achalasia is a rare disorder that makes it d...   
2  ['', 

In [5]:
graph = GraphDatabase.driver(NEO4J_URI, auth=(NEO4J_USERNAME, NEO4J_PASSWORD))

In [145]:

# Function to create a node
def create_node(tx, label, properties):
    query = f"CREATE (n:{label} {{{', '.join([f'{k}: ${k}' for k in properties.keys()])}}}) RETURN n"
    return tx.run(query, **properties).single().value()

# Function to create a relationship
def create_relationship(tx, start_node, rel_type, end_node):
    query = f"MATCH (a), (b) WHERE id(a) = {start_node.element_id} AND id(b) = {end_node.element_id} CREATE (a)-[r:{rel_type}]->(b) RETURN type(r)"
    return tx.run(query).single().value()

# Function to process the data and create the knowledge graph
def process_data(data):
    with graph.session() as session:
        # Create nodes for diseases
        for disease in data:
            disease_node = session.write_transaction(create_node, "Disease", {
                "name": disease["name"],
                "link": disease["link"]
            })

            # Create nodes for disease components and relationships
            for component, value in disease.items():
                if component != "name" and component != "link":
                    component_node = session.write_transaction(create_node, component.capitalize(), {
                        "value": value
                    })
                    session.write_transaction(create_relationship, disease_node, component, component_node)

# Process the data
with open("data/cleaned_disease_components.csv", "r") as f:
    import csv
    reader = csv.DictReader(f)
    process_data(list(reader))

C:\Users\shail\AppData\Local\Temp\ipykernel_23696\2362372248.py:16: DeprecationWarning: write_transaction has been renamed to execute_write
  disease_node = session.write_transaction(create_node, "Disease", {
C:\Users\shail\AppData\Local\Temp\ipykernel_23696\2362372248.py:24: DeprecationWarning: write_transaction has been renamed to execute_write
  component_node = session.write_transaction(create_node, component.capitalize(), {
C:\Users\shail\AppData\Local\Temp\ipykernel_23696\2362372248.py:27: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(create_relationship, disease_node, component, component_node)
C:\Users\shail\AppData\Local\Temp\ipykernel_23696\2362372248.py:8: DeprecationWarning: `id` is deprecated, use `element_id` instead
  query = f"MATCH (a), (b) WHERE id(a) = {start_node.id} AND id(b) = {end_node.id} CREATE (a)-[r:{rel_type}]->(b) RETURN type(r)"
Received notification from DBMS server: {severity: WARNING} {code: Neo.Clie

In [ ]:
# Close the Neo4j connection
graph.close()

In [35]:
import pandas as pd
import json

# Load the data into a pandas DataFrame
df = pd.read_csv("disease_components.csv.")


# Function to clean special characters
def clean_text(text):
    if isinstance(text, str):
        return text.replace('"', '').replace("'", "").replace('[', '').replace(']', '').replace('\u2014', ' ').strip()
    return text

# Apply the cleaning function to each relevant column
df['Symptoms'] = df['Symptoms'].apply(clean_text)
df['Overview'] = df['Overview'].apply(clean_text)
df['Causes'] = df['Causes'].apply(clean_text)
df['Risk factors'] = df['Risk factors'].apply(clean_text)
df['Treatment'] = df['Treatment'].apply(clean_text)

# Combine the cleaned columns
df['About'] = df.apply(
    lambda row: json.dumps({
        'symptoms': row["Symptoms"],
        'overview': row["Overview"],
        'causes': row["Causes"],
        'risk factors': row["Risk factors"],
        'treatment': row["Treatment"]
        
    }).replace('\"', '\''),  # Removes escaped quotes if any remain,
    axis=1
)

df = df.drop(columns=['Symptoms'])
df = df.drop(columns=['Overview'])
df = df.drop(columns=['Causes'])
df = df.drop(columns=['Risk factors'])
df = df.drop(columns=['Treatment'])

print(df)
# Write the cleaned data back to a file
df.to_csv("clean_disease_components.csv", index=False)


                                                   name  \
0                                  Acanthosis nigricans   
1                                             Achalasia   
2                               Achilles tendon rupture   
3                               Acute coronary syndrome   
4                                           Adenomyosis   
...                                                 ...   
1178                                               Yips   
1179                                         Zika virus   
1180                         Zollinger-Ellison syndrome   
1181        Zoster (See: Zoster, also known asShingles)   
1182  22q11.2 deletion syndrome (See: 22q11.2 deleti...   

                                                   link  \
0     https://www.mayoclinic.org/diseases-conditions...   
1     https://www.mayoclinic.org/diseases-conditions...   
2     https://www.mayoclinic.org/diseases-conditions...   
3     https://www.mayoclinic.org/diseases-conditions...

In [6]:
folder_path = "demo_graph_documents"

In [7]:
import time
start = 0
end = start + 10
import pickle

In [8]:
for filename in os.listdir(folder_path):
    if filename.endswith('.pkl'):
        file_path = os.path.join(folder_path, filename)
        print(f"Processing file: {file_path}")
        iteration_start_time = time.time()
        # Load the data from the .pkl file
        with open(file_path, 'rb') as f:
            graph_documents = pickle.load(f) 
        
        try:
            graph.add_graph_documents(
                graph_documents,
                baseEntityLabel=True,
                include_source=True
            )
        except:
            graph = Neo4jGraph()
            graph.add_graph_documents(
                    graph_documents,
                    baseEntityLabel=True,
                    include_source=True
                )
        
        # Record the end time of the iteration
        iteration_end_time = time.time()

        # Calculate the time taken for this iteration
        iteration_time = iteration_end_time - iteration_start_time

        # Print the time taken and the range of documents processed
        print(f"Added documents from {start} to {end} in {iteration_time:.2f} seconds")


Processing file: demo_graph_documents\demo_graph_documents_0_.pkl
Added documents from 0 to 10 in 4.83 seconds
Processing file: demo_graph_documents\demo_graph_documents_1000_.pkl
Added documents from 0 to 10 in 0.55 seconds
Processing file: demo_graph_documents\demo_graph_documents_1001_.pkl
Added documents from 0 to 10 in 0.39 seconds
Processing file: demo_graph_documents\demo_graph_documents_1002_.pkl
Added documents from 0 to 10 in 0.54 seconds
Processing file: demo_graph_documents\demo_graph_documents_1003_.pkl
Added documents from 0 to 10 in 0.29 seconds
Processing file: demo_graph_documents\demo_graph_documents_1004_.pkl
Added documents from 0 to 10 in 0.26 seconds
Processing file: demo_graph_documents\demo_graph_documents_1005_.pkl
Added documents from 0 to 10 in 0.30 seconds
Processing file: demo_graph_documents\demo_graph_documents_1006_.pkl
Added documents from 0 to 10 in 0.24 seconds
Processing file: demo_graph_documents\demo_graph_documents_1007_.pkl
Added documents from 0